### Import Python packages


In [ ]:
# ! uv pip install E:\Work\ruzt\msyrs --upgrade

In [ ]:
import macrosynergy
import pandas as pd
import numpy as np
import polars as pl
import time
import os

from macrosynergy.panel import view_timelines
from macrosynergy.management.types import QuantamentalDataFrame

### Import Python bindings - `msyrs`


In [ ]:
import msyrs

In [ ]:
DATA_FOLDER_PATH = "E:/Work/jpmaqs-data"

In [ ]:
cids_dm = "AUD.CAD.CHF.EUR.GBP.JPY.NOK.NZD.SEK.USD".split(".")
cids_em = "CLP.COP.CZK.HUF.IDR.ILS.INR.KRW.MXN.PLN.THB.TRY.TWD.ZAR".split(".")
cids = cids_dm + cids_em
cids_dux = list(set(cids) - set(["IDR", "NZD"]))
ecos = "CPIC_SA_P1M1ML12.CPIC_SJA_P3M3ML3AR.CPIC_SJA_P6M6ML6AR.CPIH_SA_P1M1ML12.CPIH_SJA_P3M3ML3AR.CPIH_SJA_P6M6ML6AR.INFTEFF_NSA.INTRGDP_NSA_P1M1ML12_3MMA.INTRGDPv5Y_NSA_P1M1ML12_3MMA.PCREDITGDP_SJA_D1M1ML12.RGDP_SA_P1Q1QL4_20QMA.RYLDIRS02Y_NSA.RYLDIRS05Y_NSA.PCREDITBN_SJA_P1M1ML12".split(
    "."
)


mkts = "DU02YXR_NSA.DU05YXR_NSA.DU02YXR_VT10.DU05YXR_VT10.EQXR_NSA.EQXR_VT10.FXXR_NSA.FXXR_VT10.FXCRR_NSA.FXTARGETED_NSA.FXUNTRADABLE_NSA".split(
    "."
)
xcats = ecos + mkts

cpi_xcats = "CPIC_SA_P1M1ML12.CPIC_SJA_P3M3ML3AR.CPIC_SJA_P6M6ML6AR.CPIH_SA_P1M1ML12.CPIH_SJA_P3M3ML3AR.CPIH_SJA_P6M6ML6AR".split(
    "."
)

tickers = [f"{c}_{x}" for c in cids for x in xcats]

In [ ]:
starttime = time.time()

big_df: pl.DataFrame = msyrs.qdf.load_qdf_from_download_bank(
    folder_path=DATA_FOLDER_PATH,
    xcats=xcats,
)
print(f"Time taken to load qdf batch: {time.time() - starttime}")

In [ ]:
big_df.estimated_size("mb")

In [ ]:
sel_cids = ["USD", "EUR", "GBP", "AUD", "CAD"]
start = "1990-01-01"
nb_start_time = time.time()

### Running with uniform weights, 2 xcats, 5 cids


In [ ]:
fx_xcats = [xc for xc in xcats if xc.startswith("FX")]
eq_xcats = [xc for xc in xcats if xc.startswith("EQ")]
starttime = time.time()

eq_df = msyrs.qdf.reduce_dataframe(
    df=big_df,
    cids=sel_cids,
    xcats=fx_xcats + eq_xcats + cpi_xcats,
    start=start,
)

fx_df = msyrs.qdf.reduce_dataframe(
    df=big_df, cids=sel_cids, start=start, xcats=fx_xcats, intersect=True
)
new_df: pl.DataFrame = msyrs.qdf.update_dataframe(df=eq_df, df_add=fx_df)

print(f"Time taken to reduce qdf: {time.time() - starttime}")

In [ ]:
_cids = ["USD", "CAD"]

_df = new_df.to_pandas()
starttime = time.time()


mx = macrosynergy.panel.linear_composite(

    df=_df,

    xcats=["EQXR_NSA", "FXXR_NSA"],
    cids=_cids,

    weights=None,

    signs=None,

    normalize_weights=False,
    start=None,
    end=None,

    blacklist=None,

    complete_xcats=False,

    complete_cids=False,

    new_xcat="COMPOSITE",

    new_cid="GLB",

)
print(f"Time taken to run linear composite: {time.time() - starttime}")


# view_timelines(QuantamentalDataFrame(mx), cids=_cids)

In [ ]:
_cids = ["USD", "CAD"]
starttime = time.time()

x = msyrs.panel.linear_composite(

    df=new_df,

    xcats=["EQXR_NSA", "FXXR_NSA"],
    cids=_cids,

    weights=None,

    signs=None,

    weight_xcats=None,

    normalize_weights=False,
    start=None,
    end=None,

    blacklist=None,

    complete_xcats=False,

    complete_cids=False,

    new_xcat="COMPOSITE",

    new_cid="GLB",

)
print(f"Time taken to run linear composite rs: {time.time() - starttime}")

# view_timelines(QuantamentalDataFrame(x.to_pandas()), cids=_cids)

### Running with variable weights


In [ ]:
_cids = ["USD", "CAD", "EUR", "AUD"]
_xcats = ["EQXR_NSA", "FXXR_NSA"]

mx = macrosynergy.panel.linear_composite(
    df=new_df.to_pandas(),
    xcats=_xcats,
    cids=_cids,
    weights=[1, 9],
    normalize_weights=False,
    new_xcat="COMPOSITE",
    new_cid="GLB",
)
x = msyrs.panel.linear_composite(
    df=new_df,
    xcats=_xcats,
    cids=_cids,
    weights=[1, 9],
    normalize_weights=False,
    new_xcat="COMPOSITE",
    new_cid="GLB",
)
view_timelines(QuantamentalDataFrame(mx), cids=_cids)
mwide = QuantamentalDataFrame(mx).to_wide().sort_index()
rwide = QuantamentalDataFrame(x.to_pandas()).to_wide().sort_index()
np.allclose((mwide - rwide).sum(axis=1), 0)

### Running with variable weights, normalized


In [ ]:
x = msyrs.panel.linear_composite(
    df=new_df,
    xcats=cpi_xcats,
    cids=_cids,
    weights=list(range(1, len(cpi_xcats) + 1)),
    normalize_weights=True,
    new_xcat="COMPOSITE",
    new_cid="GLB",
)
x.to_pandas().dropna(how="any")

In [ ]:
view_timelines(x.to_pandas().dropna(how="any"), cids=_cids)

In [ ]:
mx = macrosynergy.panel.linear_composite(
    df=new_df.to_pandas(),
    xcats=cpi_xcats,
    cids=_cids,
    weights=list(range(1, len(cpi_xcats) + 1)),
    normalize_weights=True,
    new_xcat="COMPOSITE",
    new_cid="GLB",
)
view_timelines(mx.dropna(how="any"), cids=_cids)

In [ ]:
mwide = QuantamentalDataFrame(mx).to_wide().sort_index()
rwide = QuantamentalDataFrame(x.to_pandas()).to_wide().sort_index()
np.allclose((mwide - rwide).sum(axis=1), 0)

### Running with categorical weights, normalized


In [ ]:
raise NotImplementedError("Not implemented yet")